In [2]:
%matplotlib inline
import re
import matplotlib
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score
from sklearn.multiclass import OneVsRestClassifier
from nltk.corpus import stopwords
stop_words = set(stopwords.words('english'))
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
import seaborn as sns
import pubmed_parser as pp

Let's look at one pub-med dictionary entry:

In [3]:
path_xml = pp.list_xml_path('../../data/raw') # list all xml paths under directory
pubmed_dict = pp.parse_medline_xml(path_xml[0]) # dictionary output

Load it into a dataframe and output the head

In [4]:
df = pd.DataFrame(pubmed_dict)
df.head()

title   issue   pages abstract  \
0  [Beta-blockers and arterial hypertension in th...   7(31)  2807-9            
1  [beta-blockers and high risk pregnancies. View...   7(31)  2811-2            
2  [Surface defense mechanisms of the nasal mucosa].  33(35)  1391-3            
3   [Pharmacological treatment of coronary disease].  33(44)  1721-4            
4             Treating the outpatient schizophrenic.   64(5)   48-56            

                                            journal  \
0                       La Nouvelle presse medicale   
1                       La Nouvelle presse medicale   
2  Polski tygodnik lekarski (Warsaw, Poland : 1960)   
3  Polski tygodnik lekarski (Warsaw, Poland : 1960)   
4                             Postgraduate medicine   

                       authors pubdate   pmid  \
0             Tcherdakoff|P|P|    1978  30970   
1  Dubois|D|D|;Petitcolas|J|J|    1978  30971   
2   Makowska|W|W|;Zawisza|E|E|    1978  30972   
3             Krotkiewski|A|A|    1978  30973   
4            Gelenberg|A J|AJ|    1978  30974   

                                          mesh_terms  \
0  D000319:Adrenergic beta-Antagonists; D005260:F...   
1  D000070:Acebutolol; D000319:Adrenergic beta-An...   
2  D001424:Bacterial Infections; D002633:Chemotax...   
3  D000319:Adrenergic beta-Antagonists; D003327:C...   
4  D000208:Acute Disease; D000553:Ambulatory Care...   

                         publication_types  ...  \
0                  D016428:Journal Article  ...   
1                  D016428:Journal Article  ...   
2  D016428:Journal Article; D016454:Review  ...   
3                  D016428:Journal Article  ...   
4                  D016428:Journal Article  ...   

                              doi references delete affiliations  pmc  \
0                                             False                     
1                                             False                     
2                                             False                     
3                                             False                     
4  10.1080/00325481.1978.11714969             False                     

  other_id       medline_ta nlm_unique_id issn_linking  country  
0           Nouv Presse Med       0312552    0301-1518   France  
1           Nouv Presse Med       0312552    0301-1518   France  
2               Pol Tyg Lek       9705468    0032-3756   Poland  
3               Pol Tyg Lek       9705468    0032-3756   Poland  
4              Postgrad Med       0401147    0032-5481  England  

[5 rows x 22 columns]

Get the unique mesh terms

In [28]:
mesh_terms_arr = []
[mesh_terms_arr.extend(mesh_terms.split('; ')) for mesh_terms in df.mesh_terms.to_list()]
unique_mesh_terms = set(mesh_terms_arr)
unique_mesh_terms

{'D001834:Body Water',
 'D007097:Imines',
 'D003652:Decanoic Acids',
 'D008382:Marfan Syndrome',
 'D008806:Mice, Inbred AKR',
 'D006472:Oral Hemorrhage',
 'D001115:Arecoline',
 'D014437:Typhus, Endemic Flea-Borne',
 'D001435:Bacteriophages',
 'D001429:Bacteriochlorophylls',
 'D011588:Psychology, Educational',
 'D004124:p-Dimethylaminoazobenzene',
 'D015073:2-Acetylaminofluorene',
 'D001160:Arterioles',
 'D011118:Polynucleotide Ligases',
 'D009238:N-Acetylmuramoyl-L-alanine Amidase',
 'D007165:Immunosuppression Therapy',
 'D009443:Neuritis',
 'D013167:Spondylitis, Ankylosing',
 'D004220:Disulfides',
 'D006016:Glycolates',
 'D007634:Keratitis',
 'D005003:Ethisterone',
 'D002076:Butirosin Sulfate',
 'D003300:Copper',
 'D000067956:Adenylyl Cyclase Inhibitors',
 'D009138:Musculocutaneous Nerve',
 'D000498:Allyl Compounds',
 'D000328:Adult',
 'D005750:Gastric Juice',
 'D007779:Lactobacillus acidophilus',
 'D003282:Contraceptives, Postcoital, Hormonal',
 'D002528:Cerebellar Neoplasms',
 'D007

Add the mesh terms to the dataframe as columns. This does take about 5 minutes to run per volume.

In [29]:
for mesh_term in unique_mesh_terms:
    df[mesh_term] = df.mesh_terms.apply(lambda x: 1 if mesh_term in x else 0)

/var/folders/tt/tm6_2g8s2ys845fjxspz_0wh0000gn/T/ipykernel_92842/2782943414.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[mesh_term] = df.mesh_terms.apply(lambda x: 1 if mesh_term in x else 0)
/var/folders/tt/tm6_2g8s2ys845fjxspz_0wh0000gn/T/ipykernel_92842/2782943414.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[mesh_term] = df.mesh_terms.apply(lambda x: 1 if mesh_term in x else 0)
/var/folders/tt/tm6_2g8s2ys845fjxspz_0wh0000gn/T/ipykernel_92842/2782943414.py:2: PerformanceWarning: DataFrame is highly fragment

Display the head of the dataframe to see if the mesh terms were added

In [34]:
df.head()

title   issue   pages abstract  \
0  [Beta-blockers and arterial hypertension in th...   7(31)  2807-9            
1  [beta-blockers and high risk pregnancies. View...   7(31)  2811-2            
2  [Surface defense mechanisms of the nasal mucosa].  33(35)  1391-3            
3   [Pharmacological treatment of coronary disease].  33(44)  1721-4            
4             Treating the outpatient schizophrenic.   64(5)   48-56            

                                            journal  \
0                       La Nouvelle presse medicale   
1                       La Nouvelle presse medicale   
2  Polski tygodnik lekarski (Warsaw, Poland : 1960)   
3  Polski tygodnik lekarski (Warsaw, Poland : 1960)   
4                             Postgraduate medicine   

                       authors pubdate   pmid  \
0             Tcherdakoff|P|P|    1978  30970   
1  Dubois|D|D|;Petitcolas|J|J|    1978  30971   
2   Makowska|W|W|;Zawisza|E|E|    1978  30972   
3             Krotkiewski|A|A|    1978  30973   
4            Gelenberg|A J|AJ|    1978  30974   

                                          mesh_terms  \
0  D000319:Adrenergic beta-Antagonists; D005260:F...   
1  D000070:Acebutolol; D000319:Adrenergic beta-An...   
2  D001424:Bacterial Infections; D002633:Chemotax...   
3  D000319:Adrenergic beta-Antagonists; D003327:C...   
4  D000208:Acute Disease; D000553:Ambulatory Care...   

                         publication_types  ... D003813:Dentistry  \
0                  D016428:Journal Article  ...                 0   
1                  D016428:Journal Article  ...                 0   
2  D016428:Journal Article; D016454:Review  ...                 0   
3                  D016428:Journal Article  ...                 0   
4                  D016428:Journal Article  ...                 0   

  D009555:Ninhydrin D012821:Silanes D006162:Guanylate Cyclase  \
0                 0               0                         0   
1                 0               0                         0   
2                 0               0                         0   
3                 0               0                         0   
4                 0               0                         0   

   D014361:Trypsin Inhibitors D003114:Colony-Forming Units Assay  \
0                           0                                  0   
1                           0                                  0   
2                           0                                  0   
3                           0                                  0   
4                           0                                  0   

  D000265:Adenylosuccinate Synthase D013680:Tectorial Membrane  \
0                                 0                          0   
1                                 0                          0   
2                                 0                          0   
3                                 0                          0   
4                                 0                          0   

  D008680:Metaraminol D004614:Emaciation  
0                   0                  0  
1                   0                  0  
2                   0                  0  
3                   0                  0  
4                   0                  0  

[5 rows x 10814 columns]

Get the counts of the mesh terms

In [40]:
mesh_term_counts = []
for mesh_term in unique_mesh_terms:
    mesh_term_counts.append((mesh_term, df[mesh_term].sum()))
mesh_term_counts = sorted(mesh_term_counts, key=lambda x: x[1], reverse=True)
mesh_term_df = pd.DataFrame(mesh_term_counts, columns=['mesh_term', 'count'])
mesh_term_df

mesh_term  count
0                          D006801:Humans  17259
1                         D000818:Animals  10858
2                            D008297:Male   7775
3                          D005260:Female   7299
4      D006863:Hydrogen-Ion Concentration   4507
...                                   ...    ...
10787                    D013534:Survival      1
10788                     D014853:Walkers      1
10789                     D012821:Silanes      1
10790                 D008680:Metaraminol      1
10791                  D004614:Emaciation      1

[10792 rows x 2 columns]

Plot the top 20 mesh terms

In [43]:
mesh_term_df.head(20).plot.bar(x='mesh_term', y='count', figsize=(20, 10))

<AxesSubplot: xlabel='mesh_term'>

How many mesh terms are there per article?

In [63]:

count_of_mesh_terms_per_article = df.iloc[:,22:].sum(axis=1).value_counts()


In [64]:
count_of_mesh_terms_per_article

9     2735
10    2591
8     2559
7     2476
11    2417
12    2207
6     2168
13    1838
5     1771
14    1715
4     1309
15    1278
16    1057
17     814
3      664
18     592
19     455
20     328
21     276
22     167
2      155
23     143
24     101
25      62
26      42
1       23
27      21
28      14
29       9
31       8
30       3
32       1
33       1
dtype: int64

Let's start training and testing

In [65]:
train, test = train_test_split(df, random_state=42, test_size=0.33, shuffle=True)

In [66]:
X_train = train.abstract
X_test = test.abstract
print(X_train.shape)
print(X_test.shape)

(20100,)
(9900,)


Create a pipeline with a multi label classifier

In [67]:

NB_pipeline = Pipeline([
                ('tfidf', TfidfVectorizer(stop_words=stop_words)),
                ('clf', OneVsRestClassifier(MultinomialNB(
                    fit_prior=True, class_prior=None))),
            ])

for mesh_term in unique_mesh_terms:
    print('... Processing {}'.format(mesh_term))
    # train the model using X_dtm & y
    NB_pipeline.fit(X_train, train[mesh_term])
    # compute the testing accuracy
    prediction = NB_pipeline.predict(X_test)
    print('Test accuracy is {}'.format(accuracy_score(test[mesh_term], prediction)))

... Processing D001834:Body Water
Test accuracy is 0.9992929292929293
... Processing D007097:Imines
Test accuracy is 1.0
... Processing D003652:Decanoic Acids
Test accuracy is 1.0
... Processing D008382:Marfan Syndrome
Test accuracy is 0.99989898989899
... Processing D008806:Mice, Inbred AKR
Test accuracy is 0.9987878787878788
... Processing D006472:Oral Hemorrhage
Test accuracy is 1.0
... Processing D001115:Arecoline
Test accuracy is 0.99989898989899
... Processing D014437:Typhus, Endemic Flea-Borne
Test accuracy is 1.0
... Processing D001435:Bacteriophages
Test accuracy is 0.9986868686868687
... Processing D001429:Bacteriochlorophylls
Test accuracy is 1.0
... Processing D011588:Psychology, Educational
Test accuracy is 1.0
... Processing D004124:p-Dimethylaminoazobenzene
Test accuracy is 0.99989898989899
... Processing D015073:2-Acetylaminofluorene
Test accuracy is 0.9995959595959596
... Processing D001160:Arterioles
Test accuracy is 0.99989898989899
... Processing D011118:Polynucleot

/Users/vagishvela/Projects/BGSU/bgsu_cs_thesis/.venv/lib/python3.9/site-packages/sklearn/multiclass.py:77: UserWarning: Label not 0 is present in all training examples.
  warnings.warn(


Test accuracy is 0.99989898989899
... Processing D009791:Oceanography
Test accuracy is 1.0
... Processing D004219:District of Columbia
Test accuracy is 0.9997979797979798
... Processing D010294:Parietal Bone
Test accuracy is 1.0
... Processing D014998:Y Chromosome
Test accuracy is 1.0
... Processing D015004:Yellow Fever
Test accuracy is 0.99989898989899
... Processing D012911:Snakes
Test accuracy is 0.9993939393939394
... Processing D009005:Monosaccharides
Test accuracy is 1.0
... Processing D012462:Saline Solution, Hypertonic
Test accuracy is 0.9995959595959596
... Processing D013678:Technology, Pharmaceutical
Test accuracy is 0.9997979797979798
... Processing D013565:Sympatholytics
Test accuracy is 0.9988888888888889
... Processing D006197:Hair
Test accuracy is 0.9984848484848485
... Processing D006568:Herpesvirus 1, Cercopithecine
Test accuracy is 1.0
... Processing D000443:Alcuronium
Test accuracy is 0.99989898989899
... Processing D009675:Novobiocin
Test accuracy is 0.999797979797

/Users/vagishvela/Projects/BGSU/bgsu_cs_thesis/.venv/lib/python3.9/site-packages/sklearn/multiclass.py:77: UserWarning: Label not 0 is present in all training examples.
  warnings.warn(


Test accuracy is 0.9997979797979798
... Processing D005306:Fertilization
Test accuracy is 0.9986868686868687
... Processing D013752:Tetracycline
Test accuracy is 0.9988888888888889
... Processing D004856:Postural Balance
Test accuracy is 0.9995959595959596
... Processing D000666:Amphotericin B
Test accuracy is 0.9997979797979798
... Processing D003623:Dark Adaptation
Test accuracy is 0.99989898989899
... Processing D011845:Radio
Test accuracy is 0.99989898989899
... Processing D002243:Carbolines
Test accuracy is 0.99989898989899
... Processing D014401:Tuberculosis, Urogenital
Test accuracy is 0.99989898989899
... Processing D010523:Peripheral Nervous System Diseases
Test accuracy is 0.9991919191919192
... Processing D013937:Thymidine Kinase
Test accuracy is 0.9997979797979798
... Processing D003488:Cyanogen Bromide
Test accuracy is 0.9994949494949495
... Processing D008669:Metallurgy
Test accuracy is 0.9995959595959596
... Processing D002625:Chemistry, Organic
Test accuracy is 1.0
... 

...

/Users/vagishvela/Projects/BGSU/bgsu_cs_thesis/.venv/lib/python3.9/site-packages/sklearn/multiclass.py:77: UserWarning: Label not 0 is present in all training examples.
  warnings.warn(


Test accuracy is 0.99989898989899
... Processing D004431:Ear, External
Test accuracy is 0.9997979797979798
... Processing D014624:Vaginal Fistula


/Users/vagishvela/Projects/BGSU/bgsu_cs_thesis/.venv/lib/python3.9/site-packages/sklearn/multiclass.py:77: UserWarning: Label not 0 is present in all training examples.
  warnings.warn(


Test accuracy is 0.99989898989899
... Processing D010373:Lice Infestations


KeyboardInterrupt: 